# Домашнее задание  № 5. Матричные разложения/Тематическое моделирование

### Задание № 1 (4 балла)

Попробуйте матричные разложения с 5 классификаторами - SGDClassifier, KNeighborsClassifier,  RandomForest, ExtraTreesClassifier (про него подробнее почитайте в документации, он похож на RF). Используйте и NMF и SVD. Сравните результаты на кросс-валидации и выберите лучшее сочетание.

В итоге у вас должно получиться, как минимум 8 моделей (два разложения на каждый классификатор). Используйте 1 и те же параметры кросс-валидации. Параметры векторизации, параметры K в матричных разложениях, параметры классификаторов могут быть разными между экспериментами.

Можете взять поменьше данных, если все будет обучаться слишком долго (не ставьте параметр K слишком большим в NMF, иначе точно будет слишком долго)

In [6]:
import gensim
import pandas as pd
import numpy as np
from pymorphy2 import MorphAnalyzer
#
from collections import Counter
from string import punctuation
from razdel import tokenize as razdel_tokenize
from IPython.display import Image
from IPython.core.display import HTML 
from sklearn.decomposition import TruncatedSVD, NMF, PCA, LatentDirichletAllocation
from sklearn.manifold import TSNE
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer, TfidfTransformer
from sklearn.metrics.pairwise import cosine_distances
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix
from sklearn.pipeline import Pipeline
from sklearn.model_selection import KFold, StratifiedKFold
from sklearn.neighbors import KNeighborsClassifier
import warnings
from matplotlib import pyplot as plt
import seaborn as sns
morph = MorphAnalyzer()
warnings.filterwarnings("ignore")
from sklearn.linear_model import SGDClassifier
from sklearn.preprocessing import StandardScaler


In [63]:
import pyLDAvis.gensim_models

c:\Users\user\OneDrive\Рабочий стол\учеба\notebooks\hse\lib\site-packages\past\builtins\misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload


In [7]:
data = pd.read_csv('avito_category_classification.csv')

In [8]:
# добавим лемматизацию
def normalize(text):
    normalized_text = [word.text.strip(punctuation) for word \
                                                            in razdel_tokenize(text)]
    normalized_text = [word.lower() for word in normalized_text if word and len(word) < 20 ]
    normalized_text = [morph.parse(word)[0].normal_form for word in normalized_text]
    return ' '.join(normalized_text)



In [9]:
data['description_norm'] = data['description'].apply(normalize)

In [6]:
data

category_name  \
0                     Автомобили   
1         Детская одежда и обувь   
2              Предложение услуг   
3                     Автомобили   
4                Бытовая техника   
...                          ...   
9893  Товары для детей и игрушки   
9894      Детская одежда и обувь   
9895   Одежда, обувь, аксессуары   
9896      Детская одежда и обувь   
9897             Бытовая техника   

                                            description  \
0               отличное состояние,обслужиание в салоне   
1     В отличном состоянии. Фирма KIKO. Очень теплый...   
2     Изготовление ограждений, перил,качелей, турник...   
3     Автомобиль в отличном техническом состоянии. О...   
4     Продается газовая плита "Гефест" (Белоруссия) ...   
...                                                 ...   
9893  Чтобы посмотреть весь ассортимент нашего магаз...   
9894  Весна,осень.74-80.вопросы можно в вайбер,двухс...   
9895  Кимоно Green Hill. Состояние  отличное,  рост ...   
9896  Б/у кроссовки на девочку. Носили только в спор...   
9897                            Холодильник на гарантии   

                                       description_norm  
0                отличный состояние обслужиание в салон  
1     в отличный состояние фирма kiko очень тёплый у...  
2     изготовление ограждение перила качели турников...  
3     автомобиль в отличный технический состояние од...  
4     продаваться газовый плита гефест белоруссия б ...  
...                                                 ...  
9893  чтобы посмотреть весь ассортимент наш магазин ...  
9894  весна осень 74-80 вопрос можно в вайбер двухст...  
9895  кимоно green hill состояние отличный рост 160-...  
9896  б у кроссовок на девочка носить только в спортзал  
9897                            холодильник на гарантия  

[9898 rows x 3 columns]

In [14]:
pipeline_rf_svd = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=5, max_df=0.4)),
    ('tfidf', TfidfTransformer()),
    ('svd', TruncatedSVD(500)),
    ('clf', RandomForestClassifier(n_estimators=100, max_depth=10))
])



pipeline_rf_nmf = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('clf', RandomForestClassifier(n_estimators=200, max_depth=6))
])

pipeline_etc_svd = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=5, max_df=0.4)),
    ('tfidf', TfidfTransformer()),
    ('svd', TruncatedSVD(500)),
    ('clf', ExtraTreesClassifier(n_estimators=100, max_depth=10))
])



pipeline_etc_nmf = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('clf', ExtraTreesClassifier(n_estimators=200, max_depth=6))
])

pipeline_knc_svd = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=5, max_df=0.4)),
    ('tfidf', TfidfTransformer()),
    ('svd', TruncatedSVD(500)),
    ('clf', KNeighborsClassifier())
])



pipeline_knc_nmf = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('clf', KNeighborsClassifier())
])

pipeline_sgd_svd = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=5, max_df=0.4)),
    ('tfidf', TfidfTransformer()),
    ('svd', TruncatedSVD(500)),
    ('standardscaler', StandardScaler()),
    ('sgdclassifier', SGDClassifier())
])



pipeline_sgd_nmf = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('standardscaler', StandardScaler()),
    ('sgdclassifier', SGDClassifier())
])

In [15]:
print(pipeline_etc_nmf)

Pipeline(steps=[('bow',
                 CountVectorizer(max_df=0.3, min_df=3,
                                 tokenizer=<function <lambda> at 0x000002215AC8CF28>)),
                ('tfidf', TfidfTransformer()),
                ('decomposition', NMF(n_components=100)),
                ('clf', ExtraTreesClassifier(max_depth=6, n_estimators=200))])


In [27]:
pipelines = [pipeline_rf_svd, pipeline_rf_nmf, pipeline_etc_svd, 
pipeline_etc_nmf, pipeline_knc_svd, pipeline_knc_nmf, pipeline_sgd_svd,pipeline_sgd_nmf]


In [16]:
def eval_table(X, y, pipeline, N=6):

    labels = list(set(y))

    fold_metrics = pd.DataFrame(index=labels)

    kfold = StratifiedKFold(n_splits=N, shuffle=True, )
    
    for i, (train_index, test_index) in enumerate(kfold.split(X, y)):
        pipeline.fit(X[train_index], y[train_index])
        preds = pipeline.predict(X[test_index])
        fold_metrics[f'f1_{i}'] = f1_score(y[test_index], preds, labels=labels, average=None)

    
    # чуточку модифицируем функцию, чтобы получить f1

    f1 = np.mean(fold_metrics[[f'f1_{i}' for i in range(N)]].mean(axis=1).round(2))
    
    
    return f1

In [25]:
f1dict = Counter()

In [29]:
for i in pipelines:
    try:
        f1dict[str(i.named_steps)]=eval_table(data['description_norm'], data['category_name'], i)
    except:
        print(str(i.named_steps))

Итак, наш победитель - SGD + SVD. Ура!

In [31]:
f1dict.most_common(1)

[("{'bow': CountVectorizer(max_df=0.4, min_df=5, ngram_range=(1, 2),\n                tokenizer=<function <lambda> at 0x000002215B480400>), 'tfidf': TfidfTransformer(), 'svd': TruncatedSVD(n_components=500), 'standardscaler': StandardScaler(), 'sgdclassifier': SGDClassifier()}",
  0.6839999999999999)]

### Задание № 2 (6 баллов)

В Gensim тоже можно добавить нграммы и tfidf. Постройте 1 модель без них (как в семинаре) и еще 3 модели (1 с нграммами, 1 с tfidf и 1 с нграммами и с tfidf). Сранивте качество с помощью метрик (перплексия, когерентность) и на глаз. Определите лучшую модель. Для каждой модели выберите 1 самую красивую на ваш взгляд тему.

Используйте данные википедии из семинара. Можете взять поменьше данных, если все обучается долго.

Важное требование - получившиеся модели не должны быть совсем плохими. Если хороших тем не получается, попробуйте настроить гиперпараметры, отфильтровать словарь по-другому. 

In [218]:
texts = open('wiki_data.txt', encoding='utf-8').read().splitlines()
texts = ([normalize(text) for text in texts])
texts = [text.split() for text in texts]

In [219]:
dictinary = gensim.corpora.Dictionary(texts)
dictinary.filter_extremes(no_above=0.1, no_below=10)
dictinary.compactify()

In [220]:
corpus = [dictinary.doc2bow(text) for text in texts]

In [80]:
corpus

[[(0, 1),
  (1, 1),
  (2, 1),
  (3, 1),
  (4, 2),
  (5, 1),
  (6, 1),
  (7, 1),
  (8, 1),
  (9, 1),
  (10, 1),
  (11, 1),
  (12, 1),
  (13, 4),
  (14, 1),
  (15, 1),
  (16, 1),
  (17, 1),
  (18, 1),
  (19, 1),
  (20, 2),
  (21, 1),
  (22, 1),
  (23, 1),
  (24, 1),
  (25, 1),
  (26, 4),
  (27, 1),
  (28, 1),
  (29, 1),
  (30, 1),
  (31, 2),
  (32, 1),
  (33, 2),
  (34, 4),
  (35, 1),
  (36, 2),
  (37, 1),
  (38, 1),
  (39, 1),
  (40, 1),
  (41, 11),
  (42, 2),
  (43, 3),
  (44, 1),
  (45, 1),
  (46, 1),
  (47, 1),
  (48, 1),
  (49, 2),
  (50, 1),
  (51, 1),
  (52, 1),
  (53, 1),
  (54, 4),
  (55, 1),
  (56, 1),
  (57, 1),
  (58, 3),
  (59, 2),
  (60, 1),
  (61, 1),
  (62, 1),
  (63, 1),
  (64, 2),
  (65, 2),
  (66, 1),
  (67, 1),
  (68, 1),
  (69, 2),
  (70, 1),
  (71, 1),
  (72, 2),
  (73, 5),
  (74, 5),
  (75, 1),
  (76, 1),
  (77, 8),
  (78, 1),
  (79, 1),
  (80, 6),
  (81, 1),
  (82, 15),
  (83, 8),
  (84, 1),
  (85, 1),
  (86, 1),
  (87, 1),
  (88, 1),
  (89, 2),
  (90, 1),
  (91, 

In [221]:
lda = gensim.models.LdaModel(corpus, 100, alpha='asymmetric', id2word=dictinary, passes=10)

In [222]:
pyLDAvis.enable_notebook()

In [205]:
pyLDAvis.gensim_models.prepare(lda, corpus, dictinary)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
71    -0.116307  0.241727       1        1  7.076677
97    -0.122157  0.052452       2        1  3.419909
94    -0.157260 -0.065656       3        1  3.159211
69    -0.143536  0.110482       4        1  2.970905
76    -0.183629 -0.087827       5        1  2.854831
...         ...       ...     ...      ...       ...
70     0.145001 -0.030952      96        1  0.129963
57     0.114074 -0.038245      97        1  0.128819
50     0.123982 -0.062082      98        1  0.123971
42     0.157431 -0.046900      99        1  0.109130
28     0.148022 -0.023019     100        1  0.070811

[100 rows x 5 columns], topic_info=             Term        Freq       Total  Category  logprob  loglift
1824        фильм  868.000000  868.000000   Default  30.0000  30.0000
100   олимпийский  951.000000  951.000000   Default  29.0000  29.0000
877      компания  801.000000  801.000000   Default  28.0000  28.0000
4368         уезд  912.000000  912.000000   Default  27.0000  27.0000
2272            н  609.000000  609.000000   Default  26.0000  26.0000
...           ...         ...         ...       ...      ...      ...
3758     нью-йорк    0.010680  126.475576  Topic100 -10.5334  -2.1265
2979     означать    0.010608  135.315856  Topic100 -10.5402  -2.2008
586        период    0.010513  549.629211  Topic100 -10.5492  -3.6115
2357    положение    0.010488  207.803809  Topic100 -10.5516  -2.6412
2250       конный    0.010483   70.576998  Topic100 -10.5521  -1.5618

[5099 rows x 6 columns], token_table=      Topic      Freq Term
term                      
3352      1  0.059625    0
3352      3  0.536621    0
3352     37  0.187391    0
3352     78  0.204427    0
2697     34  0.225206  0,1
...     ...       ...  ...
5844     37  0.223771    −
5844     65  0.402788    −
5844     66  0.044754    −
5844     92  0.179017    −
5844     97  0.089508    −

[21979 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[72, 98, 95, 70, 77, 100, 86, 66, 20, 42, 26, 19, 55, 7, 9, 15, 11, 35, 56, 38, 13, 27, 53, 2, 78, 21, 54, 24, 89, 48, 47, 14, 69, 1, 64, 67, 32, 84, 59, 25, 61, 76, 5, 94, 18, 41, 34, 10, 22, 45, 80, 52, 99, 85, 79, 96, 37, 30, 17, 3, 39, 49, 28, 36, 63, 8, 44, 16, 93, 40, 6, 87, 31, 83, 62, 88, 91, 57, 75, 97, 73, 65, 12, 92, 82, 81, 33, 23, 46, 90, 4, 74, 60, 50, 68, 71, 58, 51, 43, 29])

In [223]:

ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.2) # threshold можно подбирать
p = gensim.models.phrases.Phraser(ph)
ngrammed_texts = p[texts] 

# ! не забудьте, что далее вам нужно будет использовать ngrammed_texts

In [224]:
[text for text in ngrammed_texts[:1]]

[['новостройка',
  'нижегородский_область',
  'новостро́йка',
  '—',
  'сельский',
  'посёлок',
  'в',
  'дивеевский_район',
  'нижегородский_область',
  'входить_в',
  'состав_сатисский',
  'сельсовет',
  'посёлок_расположить',
  'в',
  '12,5',
  'км_к',
  'юг_от',
  'село_дивеево',
  'и',
  '1_км',
  'к_запад',
  'от',
  'город_саров',
  'на_право',
  'берег_река',
  'вичкинза',
  'правый_приток',
  'река_сатис',
  'окружить',
  'смешанный_лес',
  'соединить',
  'асфальтовый_дорога',
  'с',
  'посёлок',
  'цыгановка',
  '1,5_км',
  'и',
  'грунтовый_просёлочный',
  'дорога',
  'с',
  'посёлок_сатис',
  '3,5_км',
  'название',
  'новостройка',
  'являться',
  'сугубо',
  'официальный',
  'местный_население',
  'использовать',
  'исключительно',
  'альтернативный',
  'название',
  '—',
  'хитрый',
  'употребляться_языковой',
  'оборот',
  '«_…',
  'на',
  'хитрый',
  '»',
  'ранее',
  'использовать',
  'название',
  '—',
  'песчаный',
  'известковый',
  'основать_в',
  '1920-й_год',
  

In [225]:
dict_ngram = gensim.corpora.Dictionary(ngrammed_texts)

In [226]:
dict_ngram.filter_extremes(no_above=0.1, no_below=10)
dict_ngram.compactify()

In [227]:
corpus_ngram = [dictinary.doc2bow(text) for text in ngrammed_texts]

In [228]:
lda_ngram = gensim.models.LdaModel(corpus_ngram, 100,alpha='asymmetric',id2word=dict_ngram, passes=10)

In [229]:
lda_ngram.print_topics()

[(99,
  '0.048*"математика" + 0.037*"можно_увидеть" + 0.034*"облучение" + 0.030*"эллен" + 0.028*"переименовать_в" + 0.025*"куда" + 0.024*"в_результат" + 0.023*"уйти_из" + 0.022*"10" + 0.020*"село"'),
 (98,
  '0.257*"земельный_владение" + 0.253*"бассейн_река" + 0.067*"чудом" + 0.039*"свой_очередь" + 0.026*"лес" + 0.022*"похожий_на" + 0.021*"2006_год" + 0.017*"свердловск" + 0.014*"метр_от" + 0.010*"учиться_в"'),
 (97,
  '0.054*"2_км" + 0.018*"причастность_к" + 0.015*"фред" + 0.014*"перелом" + 0.012*"размер" + 0.012*"ликвидировать" + 0.011*"дивизия" + 0.010*"строительный_работа" + 0.010*"2015_г" + 0.009*"современный"'),
 (96,
  '0.015*"существовать" + 0.015*"сельский" + 0.014*"дать" + 0.014*"пройти" + 0.011*"1968" + 0.010*"следовать" + 0.010*"список" + 0.009*"обозначать" + 0.009*"элемент" + 0.009*"ощущаться"'),
 (95,
  '0.085*"харьковский_район" + 0.054*"премьера_состояться" + 0.026*"новостройка" + 0.017*"обнаружить" + 0.016*"монастырь" + 0.012*"англия_победитель" + 0.011*"результат" + 0.

In [230]:
pyLDAvis.gensim_models.prepare(lda_ngram, corpus_ngram, dict_ngram)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
34     0.119780  0.211840       1        1  4.834912
2      0.040804  0.170985       2        1  3.947122
63     0.202964  0.028513       3        1  3.733084
15     0.035102  0.178633       4        1  3.605777
45     0.053900  0.127040       5        1  3.097597
...         ...       ...     ...      ...       ...
43    -0.095085 -0.070963      96        1  0.179506
72    -0.016334 -0.097524      97        1  0.161754
80    -0.078202 -0.091093      98        1  0.153341
71    -0.058362 -0.095159      99        1  0.122926
79    -0.080607 -0.083266     100        1  0.104589

[100 rows x 5 columns], topic_info=                       Term         Freq        Total  Category  logprob  \
5974         бомбардировщик  8318.000000  8318.000000   Default  30.0000   
1787               1877_год  6061.000000  6061.000000   Default  29.0000   
16019                разгон  3478.000000  3478.000000   Default  28.0000   
9992         быть_удостоить  2867.000000  2867.000000   Default  27.0000   
17811            привлечь_к  2825.000000  2825.000000   Default  26.0000   
...                     ...          ...          ...       ...      ...   
6761           под_давление     3.067524   247.241875  Topic100  -6.3110   
2971             сведение_о     3.115621   430.586149  Topic100  -6.2955   
10665               ещё_раз     2.021304    50.447951  Topic100  -6.7282   
10513          добраться_до     2.052575    68.566605  Topic100  -6.7128   
7740   первый_всероссийский     1.271140   166.832408  Topic100  -7.1920   

       loglift  
5974   30.0000  
1787   29.0000  
16019  28.0000  
9992   27.0000  
17811  26.0000  
...        ...  
6761    2.4734  
2971    1.9342  
10665   3.6457  
10513   3.3542  
7740    1.9858  

[5331 rows x 6 columns], token_table=       Topic      Freq  Term
term                        
821       35  0.989695     0
13976     91  0.752994   0,1
822       11  0.160802   0,6
822       14  0.234684   0,6
822       26  0.108650   0,6
...      ...       ...   ...
1417      46  0.013469     €
1417      69  0.007483     €
627       11  0.043700     №
627       34  0.956449     №
8721      16  0.987066  №_15

[14893 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[35, 3, 64, 16, 46, 9, 15, 90, 95, 41, 29, 42, 38, 5, 37, 17, 47, 89, 100, 18, 63, 98, 97, 30, 91, 54, 71, 24, 96, 66, 76, 23, 85, 43, 60, 82, 52, 55, 31, 45, 27, 62, 61, 19, 11, 79, 92, 78, 20, 34, 86, 39, 50, 88, 83, 33, 57, 6, 67, 69, 1, 12, 22, 4, 51, 58, 70, 53, 40, 94, 28, 56, 25, 2, 68, 93, 10, 36, 59, 77, 13, 48, 14, 75, 65, 84, 7, 8, 99, 74, 32, 26, 49, 21, 87, 44, 73, 81, 72, 80])

In [231]:
tfidf = gensim.models.TfidfModel(corpus, id2word=dictinary, smartirs='lfc')
corpus_tfidf = tfidf[corpus]

In [232]:
lda_tfidf = gensim.models.LdaModel(corpus_tfidf, alpha='asymmetric', id2word=dictinary, passes=10)

In [233]:
lda_tfidf.print_topics()

[(98,
  '0.116*"1964" + 0.052*"япония" + 0.049*"1968" + 0.000*"улыбка" + 0.000*"сфинкс" + 0.000*"третьяковский" + 0.000*"сухость" + 0.000*"собиратель" + 0.000*"утренний" + 0.000*"чувствительность"'),
 (99,
  '0.033*"армянский" + 0.029*"армения" + 0.008*"юлиан" + 0.003*"359" + 0.002*"евфрат" + 0.000*"третьяковский" + 0.000*"царскосельский" + 0.000*"чувствительность" + 0.000*"собиратель" + 0.000*"улыбка"'),
 (96,
  '0.000*"собиратель" + 0.000*"собачка" + 0.000*"царскосельский" + 0.000*"утренний" + 0.000*"улыбка" + 0.000*"третьяковский" + 0.000*"сфинкс" + 0.000*"сухость" + 0.000*"спокойствие" + 0.000*"карфаген"'),
 (97,
  '0.009*"бесплатный" + 0.005*"видеокарта" + 0.004*"epic" + 0.000*"сфинкс" + 0.000*"чувствительность" + 0.000*"царскосельский" + 0.000*"утренний" + 0.000*"улыбка" + 0.000*"третьяковский" + 0.000*"коста-риканский"'),
 (95,
  '0.029*"святой" + 0.017*"собор" + 0.012*"алтарь" + 0.011*"базилика" + 0.008*"романский" + 0.008*"готический" + 0.007*"колокол" + 0.007*"богоматерь" + 0

In [234]:
pyLDAvis.gensim_models.prepare(lda_tfidf, corpus_tfidf, dictinary, mds='mmds')

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0     -0.285671  0.303012       1        1  64.705899
1     -0.173187 -0.505279       2        1   6.962018
3     -0.478917 -0.352507       3        1   4.749520
2      0.552392  0.007565       4        1   3.160049
4      0.067980  0.476019       5        1   1.845663
...         ...       ...     ...      ...        ...
90     0.004442  0.001288      96        1   0.057323
97     0.002320  0.004029      97        1   0.057102
94     0.004095  0.001869      98        1   0.056480
92     0.004442  0.001288      99        1   0.056199
96     0.004442  0.001288     100        1   0.054079

[100 rows x 5 columns], topic_info=               Term        Freq       Total  Category  logprob  loglift
10109   житомирский  331.000000  331.000000   Default  30.0000  30.0000
2018         снукер  496.000000  496.000000   Default  29.0000  29.0000
4118         летний  248.000000  248.000000   Default  28.0000  28.0000
1629            код  261.000000  261.000000   Default  27.0000  27.0000
2860           1952  319.000000  319.000000   Default  26.0000  26.0000
...             ...         ...         ...       ...      ...      ...
25            возле    0.003553    9.035740  Topic100  -9.9626  -0.3188
26     вознесенский    0.003553    4.033001  Topic100  -9.9626   0.4879
27          возраст    0.003553   25.208431  Topic100  -9.9626  -1.3448
28           вперёд    0.003553    6.703776  Topic100  -9.9626  -0.0203
29        грунтовый    0.003553    4.488393  Topic100  -9.9626   0.3809

[5029 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
12013     53  0.511114      0,9
841        1  0.720655      000
841        2  0.235851      000
841       16  0.039308      000
0          1  0.560077      1,2
...      ...       ...      ...
15264     55  0.622999      ярл
5682      11  0.872815     ярус
8987      10  0.759107  ёмкость
17876      5  0.788117        ―
2525      19  0.889781        ‘

[1916 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 4, 3, 5, 29, 8, 57, 6, 17, 7, 15, 55, 10, 74, 9, 75, 54, 11, 45, 38, 24, 13, 12, 14, 21, 18, 23, 90, 26, 27, 19, 16, 49, 65, 20, 22, 33, 25, 28, 32, 34, 30, 59, 31, 35, 42, 37, 36, 94, 88, 40, 70, 39, 44, 89, 47, 41, 60, 43, 46, 51, 72, 48, 56, 61, 50, 63, 53, 99, 52, 96, 79, 58, 62, 81, 92, 68, 71, 64, 69, 66, 67, 85, 82, 76, 83, 100, 77, 84, 73, 78, 80, 87, 86, 91, 98, 95, 93, 97])

In [235]:
tfidf_ngram = gensim.models.TfidfModel(corpus_ngram, id2word=dict_ngram, smartirs='lfc')
corpus_tfidf_ngram = tfidf_ngram[corpus_ngram]

In [236]:
corpus_tfidf_ngram

In [237]:
lda_tfidf_ngram = gensim.models.LdaModel(corpus_tfidf_ngram, alpha='asymmetric', id2word=dict_ngram, passes=10)

In [238]:
lda_tfidf_ngram.print_topics()

[(99,
  '0.000*"1813" + 0.000*"арифметика" + 0.000*"подлежащее" + 0.000*"почтовый_служба" + 0.000*"практически_всегда" + 0.000*"призывный" + 0.000*"1760_год" + 0.000*"некоторый_страна" + 0.000*"вятский_губерния" + 0.000*"двор_казённый"'),
 (98,
  '0.000*"1813" + 0.000*"арифметика" + 0.000*"подлежащее" + 0.000*"почтовый_служба" + 0.000*"практически_всегда" + 0.000*"призывный" + 0.000*"1760_год" + 0.000*"некоторый_страна" + 0.000*"вятский_губерния" + 0.000*"двор_казённый"'),
 (97,
  '0.000*"1813" + 0.000*"арифметика" + 0.000*"подлежащее" + 0.000*"почтовый_служба" + 0.000*"практически_всегда" + 0.000*"призывный" + 0.000*"1760_год" + 0.000*"некоторый_страна" + 0.000*"вятский_губерния" + 0.000*"двор_казённый"'),
 (95,
  '0.000*"1813" + 0.000*"арифметика" + 0.000*"подлежащее" + 0.000*"почтовый_служба" + 0.000*"практически_всегда" + 0.000*"призывный" + 0.000*"1760_год" + 0.000*"некоторый_страна" + 0.000*"вятский_губерния" + 0.000*"двор_казённый"'),
 (96,
  '0.005*"рисовать" + 0.000*"1760_год"

In [239]:
pyLDAvis.gensim_models.prepare(lda_tfidf_ngram, corpus_tfidf_ngram, dict_ngram, mds='mmds')

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0     -0.367022  0.375928       1        1  53.540546
1     -0.191955 -0.513885       2        1  10.924621
2     -0.443963 -0.338522       3        1   7.771130
3      0.543226  0.025325       4        1   4.526929
5      0.058035  0.334292       5        1   1.555379
...         ...       ...     ...      ...        ...
96    -0.001965  0.009120      96        1   0.070120
95    -0.000909  0.009200      97        1   0.068848
97    -0.000909  0.009200      98        1   0.067561
98    -0.000909  0.009200      99        1   0.066936
99    -0.000909  0.009200     100        1   0.066322

[100 rows x 5 columns], topic_info=                 Term        Freq       Total  Category  logprob  loglift
4123        разрушить  367.000000  367.000000   Default  30.0000  30.0000
2860           2002_г  244.000000  244.000000   Default  29.0000  29.0000
12077       дополнить  443.000000  443.000000   Default  28.0000  28.0000
4164   свой_сочинение  193.000000  193.000000   Default  27.0000  27.0000
14330      заграницей  315.000000  315.000000   Default  26.0000  26.0000
...               ...         ...         ...       ...      ...      ...
25      быть_освятить    0.002076    8.099042  Topic100 -10.4287  -0.9504
26        в_настоящий    0.002076    3.122796  Topic100 -10.4287   0.0026
27            в_честь    0.002076   13.857842  Topic100 -10.4287  -1.4875
28      водоснабжение    0.002076    6.155477  Topic100 -10.4287  -0.6760
29            возраст    0.002076    1.445948  Topic100 -10.4287   0.7725

[4985 rows x 6 columns], token_table=       Topic      Freq         Term
term                               
821        9  0.878333            0
822        2  0.462042          0,6
822        3  0.483044          0,6
822       56  0.042004          0,6
1          3  0.959868       1,5_км
...      ...       ...          ...
16375     63  0.814294  январь_2013
656        1  0.999756    —_топоним
627        1  0.496890            №
627        6  0.496890            №
9147      46  0.974313         №_11

[1387 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 6, 5, 7, 11, 8, 10, 9, 19, 12, 16, 25, 13, 15, 44, 17, 14, 26, 18, 27, 31, 30, 21, 24, 20, 23, 37, 22, 33, 57, 67, 28, 29, 35, 39, 63, 34, 32, 46, 36, 75, 49, 80, 45, 38, 52, 60, 40, 43, 41, 42, 62, 64, 54, 93, 65, 95, 47, 48, 51, 58, 69, 71, 50, 55, 61, 53, 56, 74, 59, 76, 66, 89, 68, 70, 72, 73, 78, 81, 77, 85, 82, 79, 87, 83, 84, 91, 86, 88, 90, 94, 92, 97, 96, 98, 99, 100])

In [240]:
def metrics_lda(model, dictinary, corpus, texts):
    topics = []
    for topic_id, topic in model.show_topics(num_topics=200, formatted=False):
        topic = [word for word, _ in topic]
        topics.append(topic)


    coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                    texts=texts, 
                                                    dictionary=dictinary, coherence='c_v')
    return coherence_model_lda.get_coherence(), np.exp2(-model.log_perplexity(corpus[:1000]))

Сразу скажу, что экспериментов было немало, и как метрики, так и адекватность не баловали высотой (и низостью соответственно для перплексии). После долгих экспериментов было решено взять корпус целиком с 10 проходами. Для tf-idf получалось очень мало тем, не сбившихся в центральный кластер, поэтому было решено изменить smartirs на lfc: показалось, что проблема в занулении(?)
Но самой удачной по метрикам и адекватности модели все равно оказалась базовая (с темами 52 - карточка персонажа и 67 - математика), на втором месте по сочетанию метрик и адекватности голая tfidf (самые интересные темы - 4 и 14 - "приключения в духе Жюля Верна" и "христианский мир" соответственно), третье занимает n-грамм модель (45 - "история успеха"), а самая неадекватная модель - тфидф+нграммы дала нам тему 16 - биография военного.

In [241]:
metrics_lda(lda, dictinary, corpus, texts)

(0.5387139804324906, 2352.8997679114773)

In [242]:
metrics_lda(lda_ngram, dict_ngram, corpus_ngram, ngrammed_texts)

(0.4358463298069873, 10433.333930139828)

In [243]:
metrics_lda(lda_tfidf, dictinary, corpus_tfidf, texts)

(0.4585781740938767, 783601494.5473543)

In [244]:
metrics_lda(lda_tfidf_ngram, dict_ngram, corpus_tfidf_ngram, ngrammed_texts)

(0.3816797085467232, 284719792284.2564)